In [2]:
import pandas as pd
import re

from dotenv import load_dotenv
from img2table.document import Image
from img2table.ocr import DocTR
from itertools import product

load_dotenv()
pd.set_option('expand_frame_repr', False)
ocr = DocTR()

In [50]:
image = Image('../NutriGenMe-Testing/monogenic-1.png')

In [51]:
extracted_tables = image.extract_tables(ocr=ocr, implicit_rows=True, borderless_tables=True, min_confidence=0)

df = []
print(len(extracted_tables))
if len(extracted_tables) > 0:
    df = extracted_tables[0].df
    for et in extracted_tables[1:]:
        df = pd.concat([df, et.df]).reset_index(drop=True)

df.head(10)

2


0                                            1                         2                                  3         4
0       None                                         None     Monogenic Diabetes or             Associated With Common      None
1  Gene Name                               Major Function                 Syndromes                     T1D and/or T2D     Refs.
2     KCNJ11     Encodes pore-forming inwardly-rectifying  PNDM (most common cause)                               E23K     42-46
3       None          potassium channel subunits (Kir6.2)       and TNDM, CHI, MODY                               None      None
4      ABCC8             Encodes regulatory SUR1 subunits  PNDM and TNDM, CHI, MODY            A1369S, 1273AGA, R1420H  46,47,52
5        GCK         A key glucose-phosphoryating enzyme;   GCK-MODY (MODY2), PNDM,  rs1799884 (G/A), rs4607517 (A/G),  75,78,79
6       None                             a glucose sensor                       CHI       3'UTR SNP, chr7:44184184-G/A      None
7     SLC2A2  Encodes GLUT2, a high-capacity facilitative                       FBS        SNPS rs5393 (AA) and rs5394    93-100
8       None                          glucose transporter                      None        (CC) in the promoter region      None
9       None                                         None                      None        and SNPS rs5400 (T1101) and      None

In [52]:
lst = []
now = []
for i in df.index:
    if not df.loc[i].isna().any():
        if len(now) > 0:
            lst.append(now)
        now = []
    now.append(i)
lst.append(now)

df.loc[0] = df.loc[0].fillna('')
dfc = pd.DataFrame(columns=df.columns)
for l in lst:
    rows = df.loc[l[0]]
    for idx in l[1:]:
        rows = rows + ' ' + df.loc[idx].fillna('')
    rows = rows.str.strip()
    dfc.loc[len(dfc)] = rows

print(dfc)

                0                                                  1                                                  2                                                  3                                4
0                                                                                                 Monogenic Diabetes or                             Associated With Common                                 
1       Gene Name                                     Major Function                                          Syndromes                                     T1D and/or T2D                            Refs.
2          KCNJ11  Encodes pore-forming inwardly-rectifying potas...       PNDM (most common cause) and TNDM, CHI, MODY                                               E23K                            42-46
3           ABCC8                   Encodes regulatory SUR1 subunits                           PNDM and TNDM, CHI, MODY                            A1369S, 1273AGA, R1420H              

#### Simple Filtering

In [12]:
def filter(row):
    concat = ' '.join(list(row))
    snp = re.findall('rs\d+', concat)
    gene = re.findall('[A-Z][A-Z0-9]{2,}', concat)

    return snp, gene

pairs = []
for i in dfc.index:
    snp_gene = filter(dfc.loc[i])
    pairs.extend(list(product(*snp_gene)))

pairs = list(set(pairs))
print(len(pairs), pairs)

118 [('rs5393', 'GLUT2'), ('rs5404', 'SNPS'), ('rs757210', 'HNF1B'), ('rs884614', 'SNPS'), ('rs2144908', 'MODY'), ('rs2144908', 'CHI'), ('rs4684847', 'T1D'), ('rs1884613', 'MODY'), ('rs1884613', 'CHI'), ('rs5393', 'SNPS'), ('rs734312', 'SNPS'), ('rs5394', 'GLUT2'), ('rs757210', 'TS4430796'), ('rs7041847', 'T1D'), ('rs6446482', 'SNPS'), ('rs7020673', 'GLIS3'), ('rs4684847', 'TZDS'), ('rs757210', 'PNDM'), ('rs5400', 'GLUT2'), ('rs7020673', 'T2D'), ('rs3818247', 'HNF4A'), ('rs4810424', 'MODY'), ('rs4810424', 'CHI'), ('rs10229583', 'R133W'), ('rs1801262', 'R111L'), ('rs1801262', 'BETA2'), ('rs10010131', 'SNPS'), ('rs10229583', 'MODY9'), ('rs5400', 'SNPS'), ('rs1801282', 'T1D'), ('rs2144908', 'HNF4A'), ('rs5393', 'FBS'), ('rs757210', 'RCAD'), ('rs10229583', 'R121W'), ('rs1801262', 'INS'), ('rs10010131', 'R456'), ('rs4684847', 'SNP'), ('rs7034200', 'T2D'), ('rs5404', 'T1101'), ('rs4607517', 'MODY'), ('rs1799884', 'MODY'), ('rs1799884', 'CHI'), ('rs4607517', 'PNDM'), ('rs6446482', 'WFS1'), ('

#### Df to JSON to LLM

In [53]:
import json

js = dfc.to_json(orient='records')

df_str = json.dumps(json.loads(js), indent=2)
print(df_str)

[
  {
    "0": "",
    "1": "",
    "2": "Monogenic Diabetes or",
    "3": "Associated With Common",
    "4": ""
  },
  {
    "0": "Gene Name",
    "1": "Major Function",
    "2": "Syndromes",
    "3": "T1D and/or T2D",
    "4": "Refs."
  },
  {
    "0": "KCNJ11",
    "1": "Encodes pore-forming inwardly-rectifying potassium channel subunits (Kir6.2)",
    "2": "PNDM (most common cause) and TNDM, CHI, MODY",
    "3": "E23K",
    "4": "42-46"
  },
  {
    "0": "ABCC8",
    "1": "Encodes regulatory SUR1 subunits",
    "2": "PNDM and TNDM, CHI, MODY",
    "3": "A1369S, 1273AGA, R1420H",
    "4": "46,47,52"
  },
  {
    "0": "GCK",
    "1": "A key glucose-phosphoryating enzyme; a glucose sensor",
    "2": "GCK-MODY (MODY2), PNDM, CHI",
    "3": "rs1799884 (G/A), rs4607517 (A/G), 3'UTR SNP, chr7:44184184-G/A",
    "4": "75,78,79"
  },
  {
    "0": "SLC2A2",
    "1": "Encodes GLUT2, a high-capacity facilitative glucose transporter",
    "2": "FBS",
    "3": "SNPS rs5393 (AA) and rs5394 (CC) i

In [8]:
from langchain_openai import ChatOpenAI

llm = ChatOpenAI(model="gpt-3.5-turbo")

In [76]:
prompt = """
# CONTEXT #
In my capacity as a genomics specialist, I have table data obtained from a published research paper in the field of genomics. The data is provided in a list of JSONs format, with each JSON object representing a single row in a tabular structure. The first JSON element in the list represents the header row of the table, containing the names of each column.
This is the data:
{}

# OBJECTIVE #
Given the provided table data, the following tasks need to be completed:

1. Identify all unique gene names present within the table. Each row can contains more than one gene name.
2. If present, extract any entries starting with "rs" (presumably representing Single Nucleotide Polymorphisms or rsIDs) that correspond to the same row as their associated gene names. Each gene name can correspond with more than one SNPs.
3. If available, extract any disease information associated with both the gene name and its corresponding SNP/rsID.

It is crucial to maintain the utmost accuracy in this process, as any false or fabricated information (hallucination) can have severe consequences for academic integrity and research credibility.
If an SNPs or Diseases is absent from the table, leave the corresponding field blank with an empty string ('').

# RESPPOSE #
The output should be a string containing list of JSON objects, each representing an entry with the following structure:
[
    {{
        "Genes": "A",
        "SNPs": ["rs123", "rs456"],
        "Diseases": "A, B, C"
    }}
]
"""

result = llm.invoke(prompt.format(df_str))
print(result.content)

[
    {
        "Genes": "KCNJ11",
        "SNPs": ["E23K"],
        "Diseases": "PNDM (most common cause) and TNDM, CHI, MODY"
    },
    {
        "Genes": "ABCC8",
        "SNPs": ["A1369S", "1273AGA", "R1420H"],
        "Diseases": "PNDM and TNDM, CHI, MODY"
    },
    {
        "Genes": "GCK",
        "SNPs": ["rs1799884 (G/A)", "rs4607517 (A/G)", "3'UTR SNP", "chr7:44184184-G/A"],
        "Diseases": "GCK-MODY (MODY2), PNDM, CHI"
    },
    {
        "Genes": "SLC2A2",
        "SNPs": ["rs5393 (AA)", "rs5394 (CC)", "rs5400 (T1101)", "rs5404 (T198T)"],
        "Diseases": "FBS"
    },
    {
        "Genes": "HNF1A/TCF1",
        "SNPs": ["G319S", "C.1522G>A (p.E508K)"],
        "Diseases": "HNF1A-MODY (MODY3), most common cause of MODY, CHI"
    },
    {
        "Genes": "HNF4A",
        "SNPs": ["rs2144908", "rs3818247", "rs884614", "rs4810424", "rs1884613"],
        "Diseases": "HNF4A MODY (MODY1), CHI"
    },
    {
        "Genes": "HNF1B/TCF2",
        "SNPs": ["rs757210 A", "

In [77]:
lst_result = eval(result.content)
lst_result

[{'Genes': 'KCNJ11',
  'SNPs': ['E23K'],
  'Diseases': 'PNDM (most common cause) and TNDM, CHI, MODY'},
 {'Genes': 'ABCC8',
  'SNPs': ['A1369S', '1273AGA', 'R1420H'],
  'Diseases': 'PNDM and TNDM, CHI, MODY'},
 {'Genes': 'GCK',
  'SNPs': ['rs1799884 (G/A)',
   'rs4607517 (A/G)',
   "3'UTR SNP",
   'chr7:44184184-G/A'],
  'Diseases': 'GCK-MODY (MODY2), PNDM, CHI'},
 {'Genes': 'SLC2A2',
  'SNPs': ['rs5393 (AA)', 'rs5394 (CC)', 'rs5400 (T1101)', 'rs5404 (T198T)'],
  'Diseases': 'FBS'},
 {'Genes': 'HNF1A/TCF1',
  'SNPs': ['G319S', 'C.1522G>A (p.E508K)'],
  'Diseases': 'HNF1A-MODY (MODY3), most common cause of MODY, CHI'},
 {'Genes': 'HNF4A',
  'SNPs': ['rs2144908', 'rs3818247', 'rs884614', 'rs4810424', 'rs1884613'],
  'Diseases': 'HNF4A MODY (MODY1), CHI'},
 {'Genes': 'HNF1B/TCF2',
  'SNPs': ['rs757210 A', 'TS4430796 A', 'TS7501939 C'],
  'Diseases': 'RCAD syndrome, or MODY5; TNDM and PNDM (rare)'},
 {'Genes': 'PDX1',
  'SNPs': ['C18R',
   'Q59L',
   'D76N',
   'R197H',
   'G212R',
   'P23

In [82]:
res_gene = []
res_snp = []
res_disease = []

for res in lst_result:
    gene = res['Genes']
    snps = res['SNPs']
    disease = res['Diseases']

    for snp in snps:
        res_gene.append(gene)
        res_snp.append(snp)
        res_disease.append(disease)

res_disease
    

['PNDM (most common cause) and TNDM, CHI, MODY',
 'PNDM and TNDM, CHI, MODY',
 'PNDM and TNDM, CHI, MODY',
 'PNDM and TNDM, CHI, MODY',
 'GCK-MODY (MODY2), PNDM, CHI',
 'GCK-MODY (MODY2), PNDM, CHI',
 'GCK-MODY (MODY2), PNDM, CHI',
 'GCK-MODY (MODY2), PNDM, CHI',
 'FBS',
 'FBS',
 'FBS',
 'FBS',
 'HNF1A-MODY (MODY3), most common cause of MODY, CHI',
 'HNF1A-MODY (MODY3), most common cause of MODY, CHI',
 'HNF4A MODY (MODY1), CHI',
 'HNF4A MODY (MODY1), CHI',
 'HNF4A MODY (MODY1), CHI',
 'HNF4A MODY (MODY1), CHI',
 'HNF4A MODY (MODY1), CHI',
 'RCAD syndrome, or MODY5; TNDM and PNDM (rare)',
 'RCAD syndrome, or MODY5; TNDM and PNDM (rare)',
 'RCAD syndrome, or MODY5; TNDM and PNDM (rare)',
 'PNDM, MODY4',
 'PNDM, MODY4',
 'PNDM, MODY4',
 'PNDM, MODY4',
 'PNDM, MODY4',
 'PNDM, MODY4',
 'PNDM, MODY4',
 'PNDM, MODY4',
 'MODY9',
 'MODY9',
 'MODY9',
 'MODY9',
 'MODY6 and PNDM',
 'MODY6 and PNDM',
 'MODY6 and PNDM',
 'WFS1, sometimes referred to as DIDMOAD',
 'WFS1, sometimes referred to as DID

In [1]:
st = '```json\n[\n    {\n        "Genes": "BCLIIA",\n        "SNPs": ["rs243021"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "ZBED3",\n        "SNPs": ["rs4457053"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "KLF14",\n        "SNPs": ["rs972283"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "TP53INP1",\n        "SNPs": ["rs896854"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "CHCHD9",\n        "SNPs": ["rs13292136"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "KCNQI",\n        "SNPs": ["rs231362"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "CENTD2",\n        "SNPs": ["rs1552224"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "HMGA2",\n        "SNPs": ["rs15313432"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "HNFIA",\n        "SNPs": ["rs7957197"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "ZFAND6",\n        "SNPs": ["rsl1634397"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "PRCI",\n        "SNPs": ["rs8042680"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "DUSP9",\n        "SNPs": ["rs5945326"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "IRSI",\n        "SNPs": ["rs7578326"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "MTNRIB",\n        "SNPs": ["rs1387153"],\n        "Diseases": ""\n    }\n]\n```'

In [3]:
st[st.find('['):st.rfind(']')+1]

'[\n    {\n        "Genes": "BCLIIA",\n        "SNPs": ["rs243021"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "ZBED3",\n        "SNPs": ["rs4457053"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "KLF14",\n        "SNPs": ["rs972283"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "TP53INP1",\n        "SNPs": ["rs896854"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "CHCHD9",\n        "SNPs": ["rs13292136"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "KCNQI",\n        "SNPs": ["rs231362"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "CENTD2",\n        "SNPs": ["rs1552224"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "HMGA2",\n        "SNPs": ["rs15313432"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "HNFIA",\n        "SNPs": ["rs7957197"],\n        "Diseases": ""\n    },\n    {\n        "Genes": "ZFAND6",\n        "SNPs": ["rsl1634397"],\n        "Diseases": ""\n    },\n    {\n   

In [22]:
from langchain_community.document_loaders.pdf import PyPDFLoader
from langchain_core.documents.base import Document
from langchain_text_splitters import TokenTextSplitter
import os

for file in os.listdir('../NutriGenMe-Testing/'):

    if file[-4:] != '.pdf':
        continue
    loader = PyPDFLoader(f"../NutriGenMe-Testing/{file}")
    pages = loader.load()

    docs = [Document('\n'.join([page.page_content for page in pages]))]
    docs[0].metadata = {'source': pages[0].metadata['source']}

    text_splitter = TokenTextSplitter.from_tiktoken_encoder(
        chunk_size=8000, chunk_overlap=0
    )
    chunks = text_splitter.split_documents(docs)
    print(len(chunks), file)

2 1-s2.0-S0002916523016155-main.pdf
3 1329.pdf
4 41467_2020_Article_15421.pdf
4 berndt2013.pdf
5 BMD.pdf
3 clock and eat timing.pdf
2 COMT breast cancer metaanalysis chinese.pdf
1 COSTAR CHATGPTPrompt _ Towards Data Science.pdf
3 dubois2010.pdf
3 EMMM-8-688.pdf
6 EMS120610.pdf
6 file.pdf
3 journal.pbio.3001547.pdf
3 lipid.pdf
7 monogenic diabetes.pdf
3 nihms-1651539.pdf
5 nihms-1792335.pdf
6 nihms-668049.pdf
4 nihms364577.pdf
4 nihms510594.pdf
4 pgen.1009952.pdf
3 PIIS0091674919313661.pdf
3 s12881-019-0830-y.pdf
4 s41576-021-00414-z (1).pdf
3 s41588-018-0047-6.pdf
8 s41588-022-01024-z (1).pdf
4 stroke genetic AHA.pdf
5 surendran2016.pdf
3 teslovich2010.pdf
1 ukmss-34421-testing.pdf
3 ukmss-34421.pdf
3 wightman2021.pdf


In [52]:
import pandas as pd
df = pd.read_excel('monogenic diabetes_16000.xlsx', sheet_name='Original')
df.tail()

Unnamed: 0    Genes      SNPs                       Diseases  \
36          36     PAX4    S1369A  hyperinsulinemic hypoglycemia   
37          37  NEUROD1      E23K               Wolfram syndrome   
38          38     WFS1  Pro12Ala                            NaN   
39          39   KIR6.2       NaN                            NaN   
40          40    GLUT2       NaN                            NaN   

                                                Title  \
36  Monogenic Diabetes: What It Teaches Us on the ...   
37  Monogenic Diabetes: What It Teaches Us on the ...   
38  Monogenic Diabetes: What It Teaches Us on the ...   
39  Monogenic Diabetes: What It Teaches Us on the ...   
40  Monogenic Diabetes: What It Teaches Us on the ...   

                           Authors     Publisher Name  Publication Year  \
36  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   
37  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   
38  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   
39  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   
40  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   

                                           Population    Sample Size  \
36  Canadian Oji-Cree, Latino, Finnish, Ashkenazi, UK  Not Specified   
37  Canadian Oji-Cree, Latino, Finnish, Ashkenazi, UK  Not Specified   
38  Canadian Oji-Cree, Latino, Finnish, Ashkenazi, UK  Not Specified   
39  Canadian Oji-Cree, Latino, Finnish, Ashkenazi, UK  Not Specified   
40  Canadian Oji-Cree, Latino, Finnish, Ashkenazi, UK  Not Specified   

                                    Study Methodology    Study Level  \
36  whole-exome sequencing, case-control and famil...  Not Specified   
37  whole-exome sequencing, case-control and famil...  Not Specified   
38  whole-exome sequencing, case-control and famil...  Not Specified   
39  whole-exome sequencing, case-control and famil...  Not Specified   
40  whole-exome sequencing, case-control and famil...  Not Specified   

                                           Conclusion  
36  The study delves into the genetic intricacies ...  
37  The study delves into the genetic intricacies ...  
38  The study delves into the genetic intricacies ...  
39  The study delves into the genetic intricacies ...  
40  The study delves into the genetic intricacies ...

In [53]:
import re
df = df.fillna('')
for i in df.index:
    snp = df.loc[i, 'SNPs'].lower()
    flag = True
    # print(snp)
    if not re.fullmatch('rs(\d)+|', snp):
        if not re.fullmatch('s(\d)+', snp):
            if not re.fullmatch('(\d)+', snp):
                flag = False
            else:
                snp = 'rs' + snp
        else:
            snp = 'r' + snp
    
    if not flag:
        df = df.drop(i)
    else:
        df.loc[i, 'SNPs'] = snp

df = df.reset_index(drop=True)
df.tail()

Unnamed: 0   Genes        SNPs                              Diseases  \
33          33   HNF4A  rs10229583            neonatal diabetes mellitus   
34          34   HNF1B   rs6467136  maturity-onset diabetes of the young   
35          35    PDX1   rs1801262           permanent neonatal diabetes   
36          39  KIR6.2                                                     
37          40   GLUT2                                                     

                                                Title  \
33  Monogenic Diabetes: What It Teaches Us on the ...   
34  Monogenic Diabetes: What It Teaches Us on the ...   
35  Monogenic Diabetes: What It Teaches Us on the ...   
36  Monogenic Diabetes: What It Teaches Us on the ...   
37  Monogenic Diabetes: What It Teaches Us on the ...   

                           Authors     Publisher Name  Publication Year  \
33  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   
34  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   
35  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   
36  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   
37  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   

                                           Population    Sample Size  \
33  Canadian Oji-Cree, Latino, Finnish, Ashkenazi, UK  Not Specified   
34  Canadian Oji-Cree, Latino, Finnish, Ashkenazi, UK  Not Specified   
35  Canadian Oji-Cree, Latino, Finnish, Ashkenazi, UK  Not Specified   
36  Canadian Oji-Cree, Latino, Finnish, Ashkenazi, UK  Not Specified   
37  Canadian Oji-Cree, Latino, Finnish, Ashkenazi, UK  Not Specified   

                                    Study Methodology    Study Level  \
33  whole-exome sequencing, case-control and famil...  Not Specified   
34  whole-exome sequencing, case-control and famil...  Not Specified   
35  whole-exome sequencing, case-control and famil...  Not Specified   
36  whole-exome sequencing, case-control and famil...  Not Specified   
37  whole-exome sequencing, case-control and famil...  Not Specified   

                                           Conclusion  
33  The study delves into the genetic intricacies ...  
34  The study delves into the genetic intricacies ...  
35  The study delves into the genetic intricacies ...  
36  The study delves into the genetic intricacies ...  
37  The study delves into the genetic intricacies ...

In [59]:
from Bio import Entrez, Seq

Entrez.email = "fadliaulawia@gmail.com"

handle = Entrez.esearch(db="gene", term='GCK [All Fields]')
record = Entrez.read(handle)
record['IdList']

['135457029', '1029', '1432', '3630', '155030', '1576', '5071', '6934', '3039', '5599', '2308', '3643', '5111', '3172', '6927', '116519', '15376', '3767', '18609', '2645']

In [54]:
import requests

data = {}

for i in df.index:
    gene = df.loc[i, 'Genes']
    snp = df.loc[i, 'SNPs']

    print(i)

    if len(data.get(gene, '')) == 0:
        url = f'https://www.ncbi.nlm.nih.gov/research/litvar2-api/variant/search/gene/{gene}'
        res = requests.get(url).content
        data[gene] = res
    
    val = data[gene]
    if len(val) != 0:
        if val.decode().find(f"'{snp}'") != -1:
            print('YES')
            continue
    
    print(gene, snp, "NO")


0
YES
1
GCK rs4607517 NO
2
YES
3
YES
4
YES
5
YES
6
YES
7
YES
8
HNF4A rs884614 NO
9
HNF4A rs4810424 NO
10
HNF4A rs1884613 NO
11
HNF1B/TCF2 rs757210 NO
12
HNF1B/TCF2 rs4430796 NO
13
HNF1B/TCF2 rs7501939 NO
14
NEUROD1IBETA2 rs1801262 NO
15
YES
16
YES
17
YES
18
YES
19
YES
20
YES
21
YES
22
YES
23
YES
24
YES
25
KCNJ11 rs2650000 NO
26
PPARG rs2144908 NO
27
INS rs3818247 NO
28
GLIS3 rs884614 NO
29
ABCC8 rs4810424 NO
30
GCK rs1884613 NO
31
SLC2A2 rs757210 NO
32
HNF1A rs4430796 NO
33
HNF4A rs10229583 NO
34
HNF1B rs6467136 NO
35
PDX1 rs1801262 NO
36
KIR6.2  NO
37
GLUT2  NO


In [ ]:
prompt = """
# CONTEXT #
In my capacity as a genomics specialist, I have table data obtained from a published research paper in the field of genomics. The data is provided in a list of JSONs format, with each JSON object representing a single row in a tabular structure.
This is the data:

[
    {{
        "Genes": "A",
        "SNPs": "rs123",
        "Diseases": "A disease"
    }}
]

# OBJECTIVE #
Given the provided table data, the following tasks need to be completed:

1. Identify all unique gene names present within the table. Each row can contains more than one gene name.
2. If present, extract any entries starting with "rs" (presumably representing Single Nucleotide Polymorphisms or rsIDs) that correspond to the same row as their associated gene names. Each gene name can correspond with more than one SNPs.
3. If available, extract any disease information associated with both the gene name and its corresponding SNP/rsID.

It is crucial to maintain the utmost accuracy in this process, as any false or fabricated information (hallucination) can have severe consequences for academic integrity and research credibility.
If an SNPs or Diseases is absent from the table, leave the corresponding field blank with an empty string ('').

# RESPONSE #
The output should only be a string containing list of JSON objects, each representing an entry with the following structure:
[
    {{
        "Genes": "A",
        "SNPs": ["rs123", "rs456"],
        "Diseases": "A disease"
    }}
]

If there is no specific extracted entities provided from the table, just leave the response with an empty lists ([]).
"""

In [1]:
from langchain_openai import ChatOpenAI

llm = ChatOpenAI(temperature=0, model_name="gpt-4-0125-preview")

result = llm.invoke("DO something").content
result

In [1]:
import pandas as pd

df = pd.read_excel("result/monogenic diabetes_8000.xlsx", sheet_name='Original')

df.head()

Unnamed: 0   Genes       SNPs                     Diseases  \
0           0     GCK  rs1799884  GCK-MODY (MODY2), PNDM, CHI   
1           1     GCK   s4607517  GCK-MODY (MODY2), PNDM, CHI   
2           2  SLC2A2     rs5393                          FBS   
3           3  SLC2A2     rs5394                          FBS   
4           4  SLC2A2     rs5400                          FBS   

                                               Title  \
0  Monogenic Diabetes: What It Teaches Us on the ...   
1  Monogenic Diabetes: What It Teaches Us on the ...   
2  Monogenic Diabetes: What It Teaches Us on the ...   
3  Monogenic Diabetes: What It Teaches Us on the ...   
4  Monogenic Diabetes: What It Teaches Us on the ...   

                          Authors     Publisher Name  Publication Year  \
0  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   
1  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   
2  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   
3  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   
4  Yisheng Yang and Lawrence Chan  Endocrine Reviews              2016   

                                          Population    Sample Size  \
0  American Indian population, Canadian Oji-Cree ...  Not Specified   
1  American Indian population, Canadian Oji-Cree ...  Not Specified   
2  American Indian population, Canadian Oji-Cree ...  Not Specified   
3  American Indian population, Canadian Oji-Cree ...  Not Specified   
4  American Indian population, Canadian Oji-Cree ...  Not Specified   

                                   Study Methodology    Study Level  \
0  Candidate gene and genome-wide association stu...  Not Specified   
1  Candidate gene and genome-wide association stu...  Not Specified   
2  Candidate gene and genome-wide association stu...  Not Specified   
3  Candidate gene and genome-wide association stu...  Not Specified   
4  Candidate gene and genome-wide association stu...  Not Specified   

                                          Conclusion  
0  The study conducted by Yisheng Yang and Lawren...  
1  The study conducted by Yisheng Yang and Lawren...  
2  The study conducted by Yisheng Yang and Lawren...  
3  The study conducted by Yisheng Yang and Lawren...  
4  The study conducted by Yisheng Yang and Lawren...

In [6]:
import json
df.fillna('', inplace=True)
json_table = df[['Genes', 'SNPs', 'Diseases']].to_json(orient='records')
str_json_table = json.dumps(json.loads(json_table), indent=2)
print(str_json_table)

[
  {
    "Genes": "GCK",
    "SNPs": "rs1799884",
    "Diseases": "GCK-MODY (MODY2), PNDM, CHI"
  },
  {
    "Genes": "GCK",
    "SNPs": "s4607517",
    "Diseases": "GCK-MODY (MODY2), PNDM, CHI"
  },
  {
    "Genes": "SLC2A2",
    "SNPs": "rs5393",
    "Diseases": "FBS"
  },
  {
    "Genes": "SLC2A2",
    "SNPs": "rs5394",
    "Diseases": "FBS"
  },
  {
    "Genes": "SLC2A2",
    "SNPs": "rs5400",
    "Diseases": "FBS"
  },
  {
    "Genes": "SLC2A2",
    "SNPs": "rs5404",
    "Diseases": "FBS"
  },
  {
    "Genes": "HNF4A",
    "SNPs": "rs2144908",
    "Diseases": "HNF4A MODY (MODY1), CHI"
  },
  {
    "Genes": "HNF4A",
    "SNPs": "S3818247",
    "Diseases": "HNF4A MODY (MODY1), CHI"
  },
  {
    "Genes": "HNF4A",
    "SNPs": "rs884614",
    "Diseases": "HNF4A MODY (MODY1), CHI"
  },
  {
    "Genes": "HNF4A",
    "SNPs": "rs4810424",
    "Diseases": "HNF4A MODY (MODY1), CHI"
  },
  {
    "Genes": "HNF4A",
    "SNPs": "s1884613",
    "Diseases": "HNF4A MODY (MODY1), CHI"
  },
  {
    

In [2]:
from process import validate


df = validate(df)

In [41]:
import requests

for i in df.index:
    snp = df.loc[i, 'SNPs']
    gene = df.loc[i, 'Genes']

    res = requests.get(f'https://www.ebi.ac.uk/gwas/rest/api/singleNucleotidePolymorphisms/{snp}/')
    try:
        res = res.json()
    except:
        print('{:<10} {:<10} Not Available'.format(gene, snp))
        continue
    lst = []
    for r in res['genomicContexts']:
        if r['gene']['geneName'] == gene:
            print('{:<10} {:<10} Match'.format(gene, snp))
            break
    else:
        print('{:<10} {:<10} Not Match'.format(gene, snp))


GCK        rs1799884  Match
GCK        rs4607517  Match
SLC2A2     rs5393     Not Available
SLC2A2     rs5394     Not Available
SLC2A2     rs5400     Match
SLC2A2     rs5404     Not Available
HNF4A      rs2144908  Not Available
HNF4A      rs3818247  Match
HNF4A      rs884614   Not Available
HNF4A      rs4810424  Not Available
HNF4A      rs1884613  Not Available
HNF1B      rs757210   Match
HNF1B      rs4430796  Match
HNF1B      rs7501939  Match
NEUROD1IBETA2 rs1801262  Not Available
WFS1       rs10010131 Match
WFS1       rs6446482  Not Available
WFS1       rs10010131 Match
WFS1       rs1801213  Not Available
WFS1       rs734312   Match
PPARG      rs1801282  Match
PPARG      rs4684847  Match
GLIS3      rs7020673  Match
GLIS3      rs7034200  Match
GLIS3      rs7041847  Match
INS        rs1799884  Not Match
GLIS3      rs5400     Not Match
ABCC8      rs2650000  Not Match
GCK        rs2144908  Not Available
SLC2A2     rs3818247  Not Match
HNF1A      rs884614   Not Available
HNF1B      rs1884

In [42]:
import requests

for i in df.index:
    snp = df.loc[i, 'SNPs']
    gene = df.loc[i, 'Genes']

    res = requests.get(f'https://eutils.ncbi.nlm.nih.gov/entrez/eutils/esummary.fcgi?db=snp&retmode=json&id={snp[2:]}').json()['result'][snp[2:]]
    if 'error' in res:
        print('{:<10} {:<10} Not Available'.format(gene, snp))
        continue
    lst = []
    for r in res['genes']:
        if r['name'] == gene:
            print('{:<10} {:<10} Match'.format(gene, snp))
            break
    else:
        print('{:<10} {:<10} Not Match'.format(gene, snp))


GCK        rs1799884  Match


GCK        rs4607517  Not Match
SLC2A2     rs5393     Match
SLC2A2     rs5394     Match
SLC2A2     rs5400     Match
SLC2A2     rs5404     Match
HNF4A      rs2144908  Match
HNF4A      rs3818247  Match
HNF4A      rs884614   Not Match
HNF4A      rs4810424  Not Match
HNF4A      rs1884613  Not Match
HNF1B      rs757210   Match
HNF1B      rs4430796  Match
HNF1B      rs7501939  Match
NEUROD1IBETA2 rs1801262  Not Match
WFS1       rs10010131 Match
WFS1       rs6446482  Match
WFS1       rs10010131 Match
WFS1       rs1801213  Match
WFS1       rs734312   Match
PPARG      rs1801282  Match
PPARG      rs4684847  Match
GLIS3      rs7020673  Match
GLIS3      rs7034200  Match
GLIS3      rs7041847  Match
INS        rs1799884  Not Match
GLIS3      rs5400     Not Match
ABCC8      rs2650000  Not Match
GCK        rs2144908  Not Match
SLC2A2     rs3818247  Not Match
HNF1A      rs884614   Not Match
HNF1B      rs1884613  Not Match
PDX1       rs757210   Not Match
PAX4       rs4430796  Not Match
NEUROD1    rs1022

In [19]:
from langchain_openai import ChatOpenAI

llm = ChatOpenAI(temperature=0, api_key=os.environ['PERPLEXITY_API_KEY'], base_url="https://api.perplexity.ai")

prompt = """
# CONTEXT #
In my capacity as a genomics specialist, I have table data containing gene names with their corresponding SNPs and diseases. The data is provided in a list of JSON format, with each JSON object representing a single row in a tabular structure. 
The problem is because the data is extracted using OCR, some gene names and SNPs may have a typo.

This is the data:
[
  {
    "Genes": "GCK",
    "SNPs": "rs1799884",
    "Diseases": "GCK-MODY (MODY2), PNDM, CHI"
  },
  {
    "Genes": "SLC242",
    "SNPs": "rs5393",
    "Diseases": "FBS"
  },
  {
    "Genes": "NEUROD1IBETA2",
    "SNPs": "rs1801262",
    "Diseases": "MODY6 and PNDM"
  },
  {
    "Genes": "WFSI",
    "SNPs": "rs6446482",
    "Diseases": "WFS1, sometimes referred to as DIDMOAD"
  },
  {
    "Genes": "GLI53",
    "SNPs": "rs7020673",
    "Diseases": "Neonatal diabetes syndrome associated with congenital hypothyroidism, and polycystic kidneys"
  },
]

# OBJECTIVE #
Given the provided table data, the following tasks need to be completed:

1. Check whether the gene name is the correct gene name. If the gene name is suspected of a typo, fix it into the correct form. If not, eliminate this row data because the gene name is invalid. 
2. If diseases are not empty, check whether the gene name corresponds with the gene names. Fix it with the correct diseases if the original disease is wrong.

# RESPONSE #
The output should only be a string containing a list of JSON objects, each representing a validated entry with the following structure:
[
    {{
        "Genes": "A",
        "SNPs": "rs123",
        "Diseases": "A disease"
    }}
]
"""

result = llm.invoke(model='mixtral-8x7b-instruct', input=prompt)
print(result.content)

To complete the given tasks, I will first provide a list of the correct gene names and their corresponding diseases. Then, I will validate the provided data and correct any discrepancies in the gene names and diseases.

Correct gene names and their corresponding diseases:

1. GCK: GCK-MODY (MODY2), PNDM, CHI
2. SLC17A4 (formerly SLC242): FBS
3. NEUROD1: MODY6 and PNDM
4. WFS1: WFS1, sometimes referred to as DIDMOAD
5. GLI3: Neonatal diabetes syndrome associated with congenital hypothyroidism, and polycystic kidneys

Validated JSON objects:

```json
[
    {
        "Genes": "GCK",
        "SNPs": "rs1799884",
        "Diseases": "GCK-MODY (MODY2), PNDM, CHI"
    },
    {
        "Genes": "SLC17A4",
        "SNPs": "rs5393",
        "Diseases": "FBS"
    },
    {
        "Genes": "NEUROD1",
        "SNPs": "rs1801262",
        "Diseases": "MODY6 and PNDM"
    },
    {
        "Genes": "WFS1",
        "SNPs": "rs6446482",
        "Diseases": "WFS1, sometimes referred to as DIDMOAD"
    },

In [20]:
from langchain_openai import ChatOpenAI

llm = ChatOpenAI(temperature=0, api_key=os.environ['PERPLEXITY_API_KEY'], base_url="https://api.perplexity.ai")

prompt = """
# CONTEXT #
In my capacity as a genomics specialist, I have table data containing gene names with their corresponding SNPs and diseases. The data is provided in a list of JSON format, with each JSON object representing a single row in a tabular structure. 
The problem is because the data is extracted using OCR, some gene names and SNPs may have a typo.

This is the data:
[
  {
    "Genes": "GCK",
    "SNPs": "rs1799884",
    "Diseases": "GCK-MODY (MODY2), PNDM, CHI"
  },
  {
    "Genes": "SLC242",
    "SNPs": "rs5393",
    "Diseases": "FBS"
  },
  {
    "Genes": "NEUROD1IBETA2",
    "SNPs": "rs1801262",
    "Diseases": "MODY6 and PNDM"
  },
  {
    "Genes": "WFSI",
    "SNPs": "rs6446482",
    "Diseases": "WFS1, sometimes referred to as DIDMOAD"
  },
  {
    "Genes": "GLI53",
    "SNPs": "rs7020673",
    "Diseases": "Neonatal diabetes syndrome associated with congenital hypothyroidism, and polycystic kidneys"
  },
]

# OBJECTIVE #
Given the provided table data, the following tasks need to be completed:

1. Check whether the gene name is the correct gene name. If the gene name is suspected of a typo, fix it into the correct form. If not, eliminate this row data because the gene name is invalid. 
2. If diseases are not empty, check whether the gene name corresponds with the gene names. Fix it with the correct diseases if the original disease is wrong.

# RESPONSE #
The output should only be a string containing a list of JSON objects, each representing a validated entry with the following structure:
[
    {{
        "Genes": "A",
        "SNPs": "rs123",
        "Diseases": "A disease"
    }}
]
"""

result = llm.invoke(model='llama-3-70b-instruct', input=prompt)
print(result.content)

Failed to batch ingest runs: TypeError('sequence item 0: expected str instance, ReadTimeoutError found')


To accomplish this task, we'll need a reference list of correct gene names and their corresponding diseases. Let's assume we have a dictionary `gene_reference` that maps correct gene names to their corresponding diseases.

Here's a Python solution using the `json` module:
```python
import json

# Reference list of correct gene names and their corresponding diseases
gene_reference = {
    "GCK": "GCK-MODY (MODY2), PNDM, CHI",
    "SLC2A2": "FBS",
    "NEUROD1": "MODY6 and PNDM",
    "WFS1": "WFS1, sometimes referred to as DIDMOAD",
    "GLIS3": "Neonatal diabetes syndrome associated with congenital hypothyroidism, and polycystic kidneys"
}

def validate_gene_name(gene_name):
    # Simple typo correction using Levenshtein distance (you can use a more advanced method if needed)
    min_distance = float('inf')
    closest_gene = None
    for ref_gene in gene_reference:
        distance = sum(el1 != el2 for el1, el2 in zip(gene_name, ref_gene))
        if distance < min_distance:
          